# Build a Long/Short Pairs Portfolio to maximum the PnL

1.   Base on **stocksInfo** and **researchData** to **identify  Pairs** and calculate **trading parameters**. 
2.   Based on **testData** to **backtest** the Pairs portfolio with **signals** and **dollarValue**
3.   Calculate the **PnL** of the backtested Pairs portfolio



# Rules
 

*   **No lookahead bias**: The testData cannot be used for Pairs identification nor the trading parameters calculations
*   **No overfitting**: The Pairs cannot be hand-picked and must be based on rules. Similarly for the trading parameters and dollarValue, apart from the obvious numbers (e.g. 0.05, 0.1, 0.5, 1, 100, 1000 etc.), they must be based on rules also.

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

%load_ext google.colab.data_table 
%matplotlib inline

# Download and import pairslib for calculating PnL
!wget https://github.com/kenwkliu/ideas/raw/master/colab/pairslib.py
import pairslib

# Load the stockInfo, researchData and testData
stocksInfo = pd.read_excel('https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/data/hkStocksQuotes.xlsx')
researchData = pd.read_csv('https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/data/researchHKStocksAdjClosePx.csv', index_col=0)
testData = pd.read_csv('https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/data/testHKStocksAdjClosePx.csv', index_col=0)


--2021-10-29 13:41:47--  https://github.com/kenwkliu/ideas/raw/master/colab/pairslib.py
Resolving github.com (github.com)... 140.82.114.4
Connecting to github.com (github.com)|140.82.114.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/pairslib.py [following]
--2021-10-29 13:41:48--  https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/pairslib.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2949 (2.9K) [text/plain]
Saving to: ‘pairslib.py’

pairslib.py         100%[===================>]   2.88K  --.-KB/s    in 0s      

2021-10-29 13:41:48 (49.8 MB/s) - ‘pairslib.py’ saved [2949/2949]



# **0. Strategies**
Problems of original strategies:

1.   Lossing big money when both stocks are in uptrend as we shorting stocks in uptrend market.
2.   Correlated currently might not imply correlated in future. Only trade stocks in same industry. 

Improvements:

1.   Check whether two stocks are related

> Simple variance (filtered by industry)

> Co-integration

2.   Check whether two stocks are both undergoing uptrend or downtrend and only accept trading range

> Using exponential moving average

> Using simple moving average

> Drawing trend line or bollinger channels 

3.   Dollar Value

> Betting More when winning money

4.   Also work with negative correlation pairs (optional)

> Going on the same direction, then short/ long the lower volatility stocks



# 0. Useful functions


In [ ]:
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)

from datetime import datetime
import numpy as np
import pandas as pd
import pandas_datareader.data as web

# Download the font to display Chinese
!wget https://github.com/kenwkliu/ideas/raw/master/colab/data/simhei.ttf
import matplotlib.pyplot as plt
from matplotlib.font_manager import FontProperties
CNFont = FontProperties(fname='/content/simhei.ttf')

# Yahoo Finance
!pip install yfinance
import yfinance as yf

# Google colab interactive table
%load_ext google.colab.data_table 
%matplotlib inline


### Helper functions
# Display the stock info in Chinese or not
def useChinese(use=True):
  # return STOCK_INFO_FILE, RESEARCH_AJD_CLOSE_FILE, TEST_AJD_CLOSE_FILE
  if use:
    return 'hkStocksQuotesChi.xlsx', 'researchHKStocksAdjClosePxChi.csv', 'testHKStocksAdjClosePxChi.csv'

  else:
    return 'hkStocksQuotes.xlsx', 'researchHKStocksAdjClosePx.csv', 'testHKStocksAdjClosePx.csv'


STOCK_INFO_FILE, RESEARCH_AJD_CLOSE_FILE, TEST_AJD_CLOSE_FILE = useChinese(False)

CHART_SIZE_X, CHART_SIZE_Y = 12, 8
SMALL_CHART_SIZE_X, SMALL_CHART_SIZE_Y = 8, 6


# Plot stock pair chart
def plotPair(df, stockA, stockB, sizeX, sizeY):
  ax1 = df[stockA].plot(label=stockA, legend=True, figsize = (sizeX, sizeY))
  ax1.set_ylim(df[stockA].min(), df[stockA].max())

  ax2 = df[stockB].plot(secondary_y=True, label=stockB, legend=True, figsize = (sizeX, sizeY))
  ax2.set_ylim(df[stockB].min(), df[stockB].max())

  ax1.legend(prop=CNFont, loc=2)
  ax2.legend(prop=CNFont, loc=1)

  plt.show()


# Plot all many Pairs at the same time
def plotManyPair(pairsDf):
  for index, row in pairsDf.iterrows():
      print('\n', index, ':', row['stockA'], 'vs', row['stockB'], '(', row['corr'], ')')
      plotPair(stocks, row['stockA'], row['stockB'], SMALL_CHART_SIZE_X, SMALL_CHART_SIZE_Y)


# Filter the correlated stock pairs with the THRESHOLD
def getCorrelatedPairs(stocksCorr, THRESHOLD=0.95):
  # filter the pairs with correlation values above the THRESHOLD
  highCorr = stocksCorr[((stocksCorr >= THRESHOLD) & (stocksCorr < 1))]
  highCorr = highCorr.unstack().sort_values(ascending=False).drop_duplicates()
  highCorr.dropna(inplace=True)
  highCorrDf = highCorr.to_frame().reset_index()
  highCorrDf.rename(columns = {'level_0':'stockA', 'level_1':'stockB', 0:'corr'}, inplace=True)

  # looks up the sectors for the stocksA and stockB
  cols = ['stockA', 'stockB', 'corr', 'sector_A', 'sector_B']
  pairsDf = highCorrDf.merge(stocksFilteredInfo[['shortName', 'sector']], how='left', left_on='stockA', right_on='shortName').merge(stocksFilteredInfo[['shortName', 'sector']], how='left', left_on='stockB', right_on='shortName', suffixes=('_A', '_B'))[cols]
  pairsDf['sameSector'] = (pairsDf['sector_A'] == pairsDf['sector_B'])
  
  return pairsDf


### back test related functions

# based on the reserch data to determind the trading params (Enter/Exit Points)
def researchTradingParams(researchData, stockA, stockB, threshold=0.05, dollarValue=10000):
  cols = [stockA, stockB]
  research_df = researchData[cols].copy()
  research_df.dropna(inplace = True)

  tradingParams = {}
  tradingParams['dollarValue'] = dollarValue

  # Calculate avgPxRatio for Exit (convergence)
  research_df['ratio'] = research_df[stockA] / research_df[stockB]
  avgPxRatio = research_df['ratio'].mean()
  tradingParams['avgPxRatio'] = avgPxRatio

  # Calculate shortA_longB_ratio for Entry (Divergence)
  shortA_longB_ratio = avgPxRatio * (1 + threshold)
  tradingParams['shortA_longB_ratio'] = shortA_longB_ratio

  # Calculate longA_shortB_ratio from Entry (Divergence)
  longA_shortB_ratio = avgPxRatio * (1 - threshold)
  tradingParams['longA_shortB_ratio'] = longA_shortB_ratio

  return tradingParams


# Determind the signal and dollarValue in the test data
# signal == -1: Long stockA Short stockB
# signal == 1: Short stockA Long stockB
# signal == 0: flat position
def backTest(testData, tradingParams, stockA, stockB):
  cols = [stockA, stockB]
  backTest_df = testData[cols].copy()
  backTest_df.dropna(inplace = True)

  # Get the tradingParams
  dollarValue = tradingParams['dollarValue']
  avgPxRatio = tradingParams['avgPxRatio']
  shortA_longB_ratio = tradingParams['shortA_longB_ratio']
  longA_shortB_ratio = tradingParams['longA_shortB_ratio']

  # Calculate the Price ratio in backTest_df
  backTest_df['pxRatio'] = backTest_df[stockA] / backTest_df[stockB]
  backTest_df['dollarValue'] = dollarValue
  
  # initialize the signal to 0
  backTest_df['signal'] = 0
  signal = 0

  # Determine the signal in each row of the backTest_df
  for index, row in backTest_df.iterrows():
    pxRatio = row['pxRatio']

    # mark signal = 1 if pxRatio > shortA_longB_ratio (Diverge outside the upper band)
    if pxRatio > shortA_longB_ratio:
      signal = 1

    # mark signal = -1 if pxRatio < longA_shortB_ratio (Diverge outside the lower band)
    elif pxRatio < longA_shortB_ratio:
      signal = -1

    else:
      # continue to mark signal = 1 if previous signal == 1 and pxRatio > avgPxRatio (Trade entered but not converge back yet)
      if signal == 1 and pxRatio > avgPxRatio:
        signal = 1

      # continue to mark signal = -1 if previous signal == -1 and pxRatio < avgPxRatio (Trade entered but not converge back yet)
      elif signal == -1 and pxRatio < avgPxRatio:
        signal = -1

      else:
        signal = 0

    backTest_df.loc[index, 'signal'] = signal

  return backTest_df


# determine pSignal and nSignal for up/down markers in plot
# pSignal and nSignal is for displaying the up/down markers in plotting chart only, they're not required for backtest calculation
def addSignalMarker(backTest_df):
  backTest_df['pSignal'] = np.where(backTest_df['signal'] == 1, backTest_df['pxRatio'], np.nan)
  backTest_df['nSignal'] = np.where(backTest_df['signal'] == -1, backTest_df['pxRatio'], np.nan)

  return backTest_df


# Combine the research and backtest for a Portfolio of Pairs
def researchAndBackTestPortfolio(pairsDf, researchData, testData, printOutput=True):
  pairsPortfolioBackTest = []

  for index, row in pairsDf.iterrows():
    stockA, stockB = row['stockA'], row['stockB']
    if printOutput: print(stockA, 'vs', stockB)
    tradingParams = researchTradingParams(researchData, stockA, stockB)
    pairsPortfolioBackTest.append(backTest(testData, tradingParams, stockA, stockB)[[stockA, stockB, 'signal', 'dollarValue']])

  return pairsPortfolioBackTest


# Download and import pairslib for calculating PnL
!wget https://github.com/kenwkliu/ideas/raw/master/colab/pairslib.py
import pairslib

--2021-10-27 06:10:42--  https://github.com/kenwkliu/ideas/raw/master/colab/data/simhei.ttf
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/data/simhei.ttf [following]
--2021-10-27 06:10:42--  https://raw.githubusercontent.com/kenwkliu/ideas/master/colab/data/simhei.ttf
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 9751960 (9.3M) [application/octet-stream]
Saving to: ‘simhei.ttf.2’

simhei.ttf.2        100%[===================>]   9.30M  --.-KB/s    in 0.07s   

2021-10-27 06:10:42 (124 MB/s) - ‘simhei.ttf.2’ saved [9751960/9751960]

The google.colab.data_table exte

# 1. Variable initiation
stocksInfo: all the background information needed

researchData: date and prices

industry_name: array of industries

sector_name: array of sectors



In [ ]:
industry_name = stocksInfo['industry'].unique()
len(industry_name)

23

In [ ]:
sector_name = stocksInfo['sector'].unique()
len(sector_name)

123

In [ ]:
researchData.shape

(249, 173)

# 2. Pairs Selection

> Cointegration between stocks



conintegration function


> input: dataframe (n, 2) stockA_price_stockB_price; String A_name; String B_name

> Output: statistics. The lower the value the higher significance of the relatinships of two stocks


Useless code

In [ ]:
#for index, row in researchData[["BABA-SW"]].iterrows():
#    print(index, row[0])
import statsmodels.api as sm

def cointegration(stockA_price_stockB_price, A_name, B_name, mean_A, mean_B, sum_var_A, sum_cov_A_B):
  slope = sum_cov_A_B / sum_var_A
# print(slope)
  interception = -slope * mean_A + mean_B
# print(interception)
  expected_y = []
  for i in range(stockA_price_stockB_price.shape[0]):
    if (np.isnan(stockA_price_stockB_price.iloc[i][0])):
      expected_y = np.append(expected_y, np.nan)
    else:
      expected_y = np.append(expected_y, slope * stockA_price_stockB_price.iloc[i][0] + interception)
# print(expected_y)

  diff_expecti_real_y = []
  for i in range(stockA_price_stockB_price.shape[0]):
    if (np.isnan(stockA_price_stockB_price.iloc[i][1])):
      diff_expecti_real_y = np.append(diff_expecti_real_y, np.nan)
    else:
      diff_expecti_real_y = np.append(diff_expecti_real_y, expected_y[i] - stockA_price_stockB_price.iloc[i][1])
# print(diff_expecti_real_y)
  diff_of_diff = diff_expecti_real_y[1:] - diff_expecti_real_y[:-1]
# print(diff_of_diff)

  compress_diff_of_diff, compress_diff_expecti_real_y = [], []
  for i in range(len(diff_of_diff)):
    if np.isnan(diff_of_diff[i]):
      pass
    else:
      compress_diff_of_diff = np.append(compress_diff_of_diff, diff_of_diff[i])
      compress_diff_expecti_real_y = np.append(compress_diff_expecti_real_y, diff_expecti_real_y[i])
  reg = sm.OLS(compress_diff_of_diff, compress_diff_expecti_real_y)
  res = reg.fit()
  t_stat = res.params[0]/ res.bse[0]
  return t_stat

# cointegration(researchData[["BABA-SW", "TENCENT"]], "BABA-SW", "TENCENT")

/usr/local/lib/python3.7/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


need 22m48s to generate the heatmap

In [ ]:
import statsmodels.tsa.stattools as ts


df = pd.DataFrame(index=researchData.columns)  
for i in researchData.columns:
  tmp = []
  for j in researchData.columns:
    if i == j:
      tmp = np.append(tmp, 0)
    else:
      compressed_A = []
      compressed_B = []
      for k in range(researchData.shape[0]):
        if np.isnan(researchData[i].iloc[k]) or np.isnan(researchData[j].iloc[k]):
          pass
        else:
          compressed_A = np.append(compressed_A, researchData[i].iloc[k])
          compressed_B = np.append(compressed_B, researchData[j].iloc[k])
      coint_tfloat, pvalue, _ = ts.coint(compressed_A, compressed_B) 
      tmp = np.append(tmp, pvalue)
# print(tmp)
  df[i] = tmp

stocksCorr = df
stocksCorr.style.background_gradient(cmap='coolwarm', axis=None)

In [ ]:
pairs = []
p_values = []
for i in df.index:
  p_value = 1
  related_stock = ""
  for k in df.index:
    if i != k and df[i].loc[k] < p_value:
      p_value = df[i].loc[k]
      related_stock = k
  related_stock = related_stock 
  pairs = np.append(pairs, related_stock)
  p_values = np.append(p_values, p_value)

pair_stocks = pd.DataFrame(index=df.index)
pair_stocks["Pairs"] = pairs
pair_stocks["P_value"] = p_values
pair_stocks.sort_values(by=["P_value"], ascending=True)

Pairs   P_value
SUNAC                      ZTE  0.000014
CHINA DONGXIANG         YEAHKA  0.000072
HENGAN INT'L      CONCH CEMENT  0.000165
YONGDA AUTO        ANTA SPORTS  0.000170
CONCH CEMENT      HENGAN INT'L  0.000198
...                        ...       ...
BROAD HOMES      GUANGDONG INV  0.061154
INNOVENT BIO       CHINA TOWER  0.062459
SJM HOLDINGS               CGS  0.068593
LI NING           CHINA JINMAO  0.069946
CSPC PHARMA               HTSC  0.092747

[173 rows x 2 columns]

Useless code

In [ ]:
"""#  mean_A = stockA_price_stockB_price[A_name].mean()
#  mean_B = stockA_price_stockB_price[B_name].mean()
#  sum_cov_A_B = 0 
#  for i in range(stockA_price_stockB_price.shape[0]):
#    if np.isnan(stockA_price_stockB_price.iloc[i][0]) or np.isnan(stockA_price_stockB_price.iloc[i][1]):
#      pass
#    else:
#      sum_cov_A_B += (stockA_price_stockB_price.iloc[i][0] - mean_A) * (stockA_price_stockB_price.iloc[i][1] - mean_B)
# print(sum_cov_A_B)
# print(i)

#  sum_var_A = 0
#  for i in range(stockA_price_stockB_price.shape[0]):
#    if (np.isnan(stockA_price_stockB_price.iloc[i][0])):
#      pass
#    else:
#      sum_var_A += (stockA_price_stockB_price.iloc[i][0] - mean_A) * (stockA_price_stockB_price.iloc[i][0] - mean_A)
# print(sum_var_A)

means = pd.DataFrame()
for i in researchData.columns:
  means[i] = [researchData[i].mean()]
# print(researchData['BABA-SW'].mean()) 
# print(means['BABA-SW'])
# print("-------------------------")


vars = pd.DataFrame()
for i in researchData.columns:
  var = 0
  for k in range(researchData[i].shape[0]):
    if  np.isnan(researchData[i].iloc[k]):
      pass
    else:
      var += (researchData[i].iloc[k] - means[i]) * (researchData[i].iloc[k] - means[i])
  vars[i] = [var]

covs = pd.DataFrame()
for i in researchData.columns:
  tmp = []
  for j in researchData.columns:
    sum_cov_A_B = 0
    for k in range(researchData[i].shape[0]):
      if np.isnan(researchData[i].iloc[k]) or np.isnan(researchData[j].iloc[k]):
        pass
      else:
        sum_cov_A_B += (researchData[i].iloc[k] - means[i]) * (researchData[j].iloc[k] - means[j])
    # print(sum_cov_A_B)
    tmp = np.append(tmp, sum_cov_A_B)
  # print(tmp)
  covs[i] = tmp

df = pd.DataFrame(index=researchData.columns)  
for i in researchData.columns:
  tmp = []
  for j in researchData.columns:
    if i == j:
      tmp = np.append(tmp, 0)
    else:
      tmp = np.append(tmp, cointegration(researchData[[i, j]], i, j, means[i], means[j], vars[i], covs[i].iloc[j]))
  df[i] = tmp

stocksCorr = df
stocksCorr.style.background_gradient(cmap='coolwarm', axis=None)"""

'#  mean_A = stockA_price_stockB_price[A_name].mean()\n#  mean_B = stockA_price_stockB_price[B_name].mean()\n#  sum_cov_A_B = 0 \n#  for i in range(stockA_price_stockB_price.shape[0]):\n#    if np.isnan(stockA_price_stockB_price.iloc[i][0]) or np.isnan(stockA_price_stockB_price.iloc[i][1]):\n#      pass\n#    else:\n#      sum_cov_A_B += (stockA_price_stockB_price.iloc[i][0] - mean_A) * (stockA_price_stockB_price.iloc[i][1] - mean_B)\n# print(sum_cov_A_B)\n# print(i)\n\n#  sum_var_A = 0\n#  for i in range(stockA_price_stockB_price.shape[0]):\n#    if (np.isnan(stockA_price_stockB_price.iloc[i][0])):\n#      pass\n#    else:\n#      sum_var_A += (stockA_price_stockB_price.iloc[i][0] - mean_A) * (stockA_price_stockB_price.iloc[i][0] - mean_A)\n# print(sum_var_A)\n\nmeans = pd.DataFrame()\nfor i in researchData.columns:\n  means[i] = [researchData[i].mean()]\n# print(researchData[\'BABA-SW\'].mean()) \n# print(means[\'BABA-SW\'])\n# print("-------------------------")\n\n\nvars = pd.DataFr

# 3a. Algo (abritrate)

> constant geometry mean of two stocks

Reason:
1.   Even two stocks are correlated, which mean they rise their price together and drop together in a similar way most of the time. The ratio between price could be broken up when the market share of the two stocks change. --> we only focus on 90days geometry mean of two stocks which implies the normally period of the released of quarterly performance. 

[improvement: change to moving geometry mean/ using cross entropy to signal a recalculation of the geometry mean]
2.   Geometric means will be a better options when considering time series

> input: pairs of stocks' price data, number of standard scores

> Algo: generate trading signals based on threshold value and pair relationships

> Output: new dataframe of squece of trading signals


In [ ]:
from scipy.stats.mstats import gmean

def signal_pre_generate(stockA_price_stockB_price, A_name, B_name, st_score):
  geo_mean_A = float(stockA_price_stockB_price[[A_name]].apply(lambda row: gmean(row[~row.isna()]), axis=0))
  geo_mean_B = float(stockA_price_stockB_price[[B_name]].apply(lambda row: gmean(row[~row.isna()]), axis=0))
  geo_ratio = geo_mean_A/ geo_mean_B
# print(geo_ratio)

  A_v_B = pd.DataFrame(index=stockA_price_stockB_price[A_name].index)
  A_v_B["pxRatio"] = stockA_price_stockB_price[A_name] / stockA_price_stockB_price[B_name]
  
  sd_A_to_B = A_v_B["pxRatio"].std()
# print(sd_A_to_B)

  A_v_B["Stock A Prices"] = stockA_price_stockB_price[A_name]
  A_v_B["Stock B Prices"] = stockA_price_stockB_price[B_name]

  shortA_longB_ratio = geo_ratio + sd_A_to_B * st_score
  longA_shortB_ratio = geo_ratio - sd_A_to_B * st_score
  signal = 0
# print(geo_ratio)
# print(shortA_longB_ratio)
# print(longA_shortB_ratio)

# Determind the signal and dollarValue in the test data
# signal == -1: Long stockA Short stockB
# signal == 1: Short stockA Long stockB
# signal == 0: flat position
  for index, row in A_v_B.iterrows():
    pxRatio = row['pxRatio']
    if pxRatio > shortA_longB_ratio:
      signal = 1

    elif pxRatio < longA_shortB_ratio:
      signal = -1

    else:
      if signal == 1 and pxRatio > geo_ratio:
        signal = 1

      elif signal == -1 and pxRatio < geo_ratio:
        signal = -1

      else:
        signal = 0

    A_v_B.loc[index, 'Signals'] = signal
  return A_v_B

signal_pre_generate(researchData[["GALAXY ENT", "BUD APAC"]], "GALAXY ENT", "BUD APAC", 1.5)

pxRatio  Stock A Prices  Stock B Prices  Signals
Date                                                         
2020-01-02  2.306269       60.077793       26.049772      0.0
2020-01-03  2.212828       58.296242       26.344673      0.0
2020-01-06  2.226185       57.553932       25.853168      0.0
2020-01-07  2.236617       58.593166       26.197224      0.0
2020-01-08  2.265903       58.692139       25.902319      0.0
...              ...             ...             ...      ...
2020-12-24  2.354823       58.750000       24.948799      0.0
2020-12-28  2.341968       57.500000       24.552000      0.0
2020-12-29  2.403688       58.299999       24.254400      0.0
2020-12-30  2.374022       59.700001       25.147200      0.0
2020-12-31  2.361919       60.450001       25.593599      0.0

[249 rows x 4 columns]

# 3b. Algo (Trend Checking)

1.   Long short MA

> Long MA > Short MA for consecutives three days --> downtrend

> Using Exponential MA

2.   Choosing Parameters

> Randomly Assign(90, 5) 90: period of release of quarterly performance; 5: reaction time for stocks price. 

> Select by heatmap

3.   Return: 1 when uptrend; -1 when downtrend; 0 when trading range.

Usage:

      yet entered market + double same trend--> not entering

      entered market + double same trend--> if winning --> continue

      entered market + double same trend--> if lossing --> terminate trade

      *current appraoch: entered market + double same trend --> continue*  

In [ ]:
import math 
def trend_calculation(stockA, stockA_name, st_score, long_trend=90, short_trend=5, alpha=1-(math.e/ math.pi)):
  long_ema = stockA.ewm(min_periods=long_trend, span=long_trend).mean()
  short_ema = stockA.ewm(min_periods=short_trend,span=short_trend).mean()
  long_ema_sd = long_ema[stockA_name].std()

  signal = 0
  signals = []
  for i in range(short_ema.shape[0]):
    if np.isnan(long_ema[stockA_name].iloc[i]):
      signals = np.append(signals, int(0))
    else:
      if short_ema[stockA_name].iloc[i] > long_ema[stockA_name].iloc[i] + long_ema_sd:
        signals = np.append(signals, int(1))
      elif short_ema[stockA_name].iloc[i] < long_ema[stockA_name].iloc[i] - long_ema_sd:
        signals = np.append(signals, int(-1))
      else:
        signals = np.append(signals, int(0))
  df = pd.DataFrame(index=long_ema.index)
  df[stockA_name] = stockA
  df["Long EMA"] = long_ema
  df["Short EMA"] = short_ema
  df["Signals"] = signals
  return df

trend_calculation(researchData[["SUNAC"]], 'SUNAC', 0.5)

SUNAC   Long EMA  Short EMA  Signals
Date                                                
2020-01-02  42.783207        NaN        NaN      0.0
2020-01-03  41.864548        NaN        NaN      0.0
2020-01-06  40.420944        NaN        NaN      0.0
2020-01-07  40.508434        NaN        NaN      0.0
2020-01-08  40.027233        NaN  40.635525      0.0
...               ...        ...        ...      ...
2020-12-24  24.977028  27.592253  24.977058     -1.0
2020-12-28  24.567568  27.525027  24.840561     -1.0
2020-12-29  25.250000  27.474475  24.977041     -1.0
2020-12-30  25.250000  27.425059  25.068027     -1.0
2020-12-31  26.023424  27.393929  25.386493     -1.0

[249 rows x 4 columns]

# 4. Algo (merging & backtest)

signal_pre_generate: return df["pxRatio", "Stock A Prices", "Stock B Price", "Signals"]

trend_calculation: return df["Stock", "Long EMA", "Short EMA", "Signals"]

afterall: return (Date, stockA, stockB, signal, dollarValue)

In [ ]:
def backTest(pair_stocks_df):
  st_score_for_ab = 1.5
  st_score_for_trend = 0.5
  pairsPortfolioBackTest = []
  for i in pair_stocks.sort_values(by=["P_value"], ascending=True).index:
    cointe = signal_pre_generate(researchData[[i, pair_stocks["Pairs"].loc[i]]], i, pair_stocks["Pairs"].loc[i], st_score_for_ab)
    df = pd.DataFrame(index=researchData.index)
    # print(researchData[i])
    # print(i)
    trend_A = trend_calculation(researchData[[i]], i, st_score_for_trend)
    trend_B = trend_calculation(researchData[[pair_stocks["Pairs"].loc[i]]], pair_stocks["Pairs"].loc[i], st_score_for_trend)
    for j in range(1, cointe.shape[0]):
      if (trend_A["Signals"].iloc[j - 1] == 1 and trend_B["Signals"].iloc[j - 1] == 1) or (trend_A["Signals"].iloc[j - 1] == -1 and trend_B["Signals"].iloc[j - 1] == -1):
        if (cointe["Signals"].iloc[j - 1] == 0):
          cointe["Signals"].iloc[j] = 0
    df[[i]] = researchData[[i]]
    df[[pair_stocks["Pairs"].loc[i]]] = researchData[[pair_stocks["Pairs"].loc[i]]]
    df["signal"] = cointe["Signals"].astype(int)
    # print(pair_stocks["P_value"].loc[i])
    if  pair_stocks["P_value"].loc[i] < 0.0005:
      df["dollarValue"] = 0
    elif pair_stocks["P_value"].loc[i] < 0.005 and pair_stocks["P_value"].loc[i] >= 0.0005:
      df["dollarValue"] = 10000
    elif pair_stocks["P_value"].loc[i] < 0.01 and pair_stocks["P_value"].loc[i] >= 0.005:
      df["dollarValue"] = 20000
    elif pair_stocks["P_value"].loc[i] < 0.03 and pair_stocks["P_value"].loc[i] >= 0.01:
      df["dollarValue"] = 10000
    elif pair_stocks["P_value"].loc[i] >= 0.03:
      df["dollarValue"] = 0
    df["dollarValue"] = df["dollarValue"].astype(int)
    pairsPortfolioBackTest.append(df)
  return pairsPortfolioBackTest

pairsPortfolioBackTest = backTest(pair_stocks)

In [ ]:
for index,row in pairsPortfolioBackTest[0].iterrows():
  print(row['dollarValue'])

# 5. Calculating overall results
pairsPortfolioBackTest[201, 4] = [Stock A's price, Stock B's price, signal, accumulated dollar value]

signal = 1 --> short A long B

signal = -1 --> long A short B


In [ ]:
# Implement your logic to construct "pairsPortfolioBackTest"
# pairsPortfolioBackTest needs to be same format as in https://colab.research.google.com/github/kenwkliu/ideas/blob/master/colab/HKStocksCorrelation.ipynb
# It is a list of backtested Pairs
# Each backtested Pairs is a dataframe with at least 5 columns (Date, stockA, stockB, signal, dollarValue)

# signal is -1, 0, 1
# signal == -1: Long stockA Short stockB
# signal == 1: Short stockA Long stockB
# signal == 0: flat position

# Calcuate the PnL of the Pairs portfolio
pnl, pnlDf = pairslib.calcPortfolio(pairsPortfolioBackTest)
pnlDf

SUNAC vs ZTE ---> $ 0.0
CHINA DONGXIANG vs YEAHKA ---> $ 0.0
HENGAN INT'L vs CONCH CEMENT ---> $ 0.0
YONGDA AUTO vs ANTA SPORTS ---> $ 0.0
CONCH CEMENT vs HENGAN INT'L ---> $ 0.0
MENGNIU DAIRY vs ZIJIN MINING ---> $ 0.0
WH GROUP vs CHINA FEIHE ---> $ 0.0
CLP HOLDINGS vs KINGSOFT ---> $ 0.0
KOOLEARN vs CONCH CEMENT ---> $ 0.0
TENCENT vs ZHONGSHENG HLDG ---> $ 0.0
XIAOMI-W vs FLAT GLASS ---> $ 0.0
ZIJIN MINING vs MENGNIU DAIRY ---> $ 0.0
PICC GROUP vs ASM PACIFIC ---> $ 0.0
GUANGDONG INV vs YEAHKA ---> $ 0.0
ZHONGSHENG HLDG vs TENCENT ---> $ 0.0
ZHAOJIN MINING vs HENGTEN NET ---> $ 756.533878833769
WYNN MACAU vs SINOPHARM ---> $ 506.4670549462719
NEWWORLDDEV-NEW vs CHINA LIFE ---> $ 219.49778474473203
WEICHAI POWER vs COMEC ---> $ 190.107677831483
COUNTRY GARDEN vs ENN ENERGY ---> $ 360.31045803009295
CGS vs EVERG HEALTH ---> $ 668.0166933859135
FLAT GLASS vs XIAOMI-W ---> $ -109.79971526439294
CHINASOFT INT'L vs GEELY AUTO ---> $ 466.1920063410929
SHK PPT vs A-LIVING ---> $ 433.63820722

stockA        stocksB  Pnl
0              SUNAC            ZTE  0.0
1    CHINA DONGXIANG         YEAHKA  0.0
2       HENGAN INT'L   CONCH CEMENT  0.0
3        YONGDA AUTO    ANTA SPORTS  0.0
4       CONCH CEMENT   HENGAN INT'L  0.0
..               ...            ...  ...
168      BROAD HOMES  GUANGDONG INV  0.0
169     INNOVENT BIO    CHINA TOWER  0.0
170     SJM HOLDINGS            CGS  0.0
171          LI NING   CHINA JINMAO  0.0
172      CSPC PHARMA           HTSC  0.0

[173 rows x 3 columns]